In [1]:
# from transformers import AutoModelForCausalLM, BitsAndBytesConfig, AutoTokenizer
from huggingface_hub import hf_hub_download, notebook_login
import numpy as np
import pandas as pd
import torch
import json
import os
import re


from sae_lens import SAE  
from transformer_lens import HookedTransformer

## Loading
- Data
- Model
- SAE

In [2]:
notebook_login()

In [3]:
DEVICE = "cuda" if torch.cuda.is_available() else "cpu"
# torch.cuda.set_manual_seed(42)
print(DEVICE)
#load the model with translens
model = HookedTransformer.from_pretrained("google/gemma-2-2b", device="cuda")

cuda


config.json:   0%|          | 0.00/818 [00:00<?, ?B/s]

model.safetensors.index.json:   0%|          | 0.00/24.2k [00:00<?, ?B/s]

model-00001-of-00003.safetensors:   0%|          | 0.00/4.99G [00:00<?, ?B/s]

model-00002-of-00003.safetensors:   0%|          | 0.00/4.98G [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/46.4k [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/4.24M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/17.5M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/636 [00:00<?, ?B/s]

Loaded pretrained model google/gemma-2-2b into HookedTransformer


In [24]:
#loading data 
animals = json.load(open("animals.json", "r"))
sing_tok = []
pairs = []
for k in animals:
    for v in animals[k]:
        try:
            sing_tok.append((model.to_single_token(v), k)) #keep the value as hyponym  and the key as the hyperonym
            #sing_tok.append((v,model.to_single_token(v) ))
            pairs.append((v,k))
        except AssertionError:
            pass

        

print(f"Number of sing tok for ANIMALS hyperonims: {len(sing_tok)}")

Number of sing tok for ANIMALS hyperonims: 111


In [10]:
#load sae  from sae lens
sae, cfg_dict, sparsity = SAE.from_pretrained(
    release = "gemma-scope-2b-pt-res-canonical",
    sae_id = "layer_25/width_16k/canonical",
    device = DEVICE
)

## Extracting features
- Formatting inputs
- Get SAE features
- Store topk activating features

In [57]:
#sae locations 1 attn heads outptuts 2 MLP outputs after RMSNorm 3 post MLP residual stream
# 'blocks.25.attn.hook_z'
# 'blocks.25.hook_mlp_out'
# 'blocks.25.hook_resid_post'
# set the target location to extract model's activation corresponding to sae's acts
target_location = 'blocks.25.hook_resid_post'


# # format inputs in a template
# template = "The {} is a {}"
# input_texts = [template.format(a) for a in animals]
input_texts = [f"The {a[0]} is a {a[1]}" for a in pairs]

# extract all activation from the given location for each input
target_act_all = [model.run_with_cache(i)[1][target_location].squeeze() for i in input_texts]
# gather sae activations
sae_act_all = [sae.encode(t) for t in target_act_all]

#get indices of sparse activated features
indices = np.stack([act.max(-1).indices.detach().cpu().numpy() for act in sae_act_all if act.shape[0] == 6])

# store the topk actiating features
top_k_ids = [act[2].topk(5).indices.detach().cpu().numpy() for act in sae_act_all]

## Check Explanations
- Download/Open explanations
- Filter explanations for the target features
- Store explanations in a dataframe

In [12]:
# download features explanations for the target layer and store them locally
if not os.path.exists("./gemma-2-2b_25-gemmascope-res-16k.json"):
    !wget https://neuronpedia-exports.s3.amazonaws.com/explanations-only/gemma-2-2b_25-gemmascope-res-16k.json

# read features explanations in a variable (list of dict)
gs_explanations = json.load(open("./gemma-2-2b_25-gemmascope-res-16k.json", "r"))

NameError: name 'os' is not defined

In [65]:
# helper function to filter the target explanations
def filter_explanation(feature_id, explanations, desc_only = False):
  """
  Helper function to filter the desired feature explanations
  feature_id: int : id of the target sae feature
  explanations: List[Dict]: the set of downloaded explanations to use
  desc_only: bool: return all metadata or only the textual description
   """
  metadata = [e for e in explanations if int(e["index"]) == feature_id][0]
  if not desc_only:
    return metadata
  else:
    return metadata["description"].strip()
  #return [e for e in explanations if int(e["index"]) == feature_id][0]#["description"]

filter_explanation(14325, gs_explanations, desc_only = True)

'numerical data and statistics related to incidents or events'

In [67]:
#extract explanations for all top k features
explanations = []
for id_set in top_k_ids:
    expl = []
    for id in id_set: #range(id_set), id_set[id]
        expl.append(filter_explanation(id, gs_explanations, desc_only = True))
    explanations.append(expl)
    # explanations.append(expl.insert(0, input_texts[id]))
print(len(explanations))

111


In [93]:
df = pd.DataFrame(explanations, columns = [f"Top{k}_feature" for k in range(1,6)], index = [",".join((a[0],i)) for a,i in zip(pairs,input_texts)])
df.to_csv("./topk_explanations2.tsv", sep = "\t")
df


Top1_feature  \
lion,The lion is a mammal                       words and phrases related to animals   
llama,The llama is a mammal        numerical data and statistics related to incid...   
rabbit,The rabbit is a mammal      numerical data and statistics related to incid...   
mongoose,The mongoose is a mammal  terms related to the performance or descriptio...   
hamster,The hamster is a mammal                 words and phrases related to animals   
...                                                                              ...   
spider,The spider is a insect      references to individual songs or personal nar...   
cricket,The cricket is a insect    references to various sports, particularly tea...   
ant,The ant is a insect            code elements related to programming and datab...   
mite,The mite is a insect          numerical data and statistics related to incid...   
bee,The bee is a insect            specific medical terms and concepts related to...   

                                                                        Top2_feature  \
lion,The lion is a mammal          technical terms and keywords related to progra...   
llama,The llama is a mammal        elements related to academic citations and aff...   
rabbit,The rabbit is a mammal                   words and phrases related to animals   
mongoose,The mongoose is a mammal  references to specific names and titles in a n...   
hamster,The hamster is a mammal    numerical data and statistics related to incid...   
...                                                                              ...   
spider,The spider is a insect      references to Spider-Man and associated themes...   
cricket,The cricket is a insect    numerical data and statistics related to incid...   
ant,The ant is a insect            specific references to parts of plants or bota...   
mite,The mite is a insect          terms and phrases related to biochemical proce...   
bee,The bee is a insect            numerical data and statistics related to incid...   

                                                                        Top3_feature  \
lion,The lion is a mammal          references to individual songs or personal nar...   
llama,The llama is a mammal                     words and phrases related to animals   
rabbit,The rabbit is a mammal      elements related to themes of social justice a...   
mongoose,The mongoose is a mammal  elements related to themes of social justice a...   
hamster,The hamster is a mammal    elements related to themes of social justice a...   
...                                                                              ...   
spider,The spider is a insect                   words and phrases related to animals   
cricket,The cricket is a insect    elements related to sports and individual athl...   
ant,The ant is a insect            numerical data and statistics related to incid...   
mite,The mite is a insect          information related to plant species and their...   
bee,The bee is a insect            information related to beekeeping practices an...   

                                                                        Top4_feature  \
lion,The lion is a mammal          elements related to themes of social justice a...   
llama,The llama is a mammal        references to individual songs or personal nar...   
rabbit,The rabbit is a mammal      technical terms and keywords related to progra...   
mongoose,The mongoose is a mammal               words and phrases related to animals   
hamster,The hamster is a mammal    references to individual songs or personal nar...   
...                                                                              ...   
spider,The spider is a insect      specific references to parts of plants or bota...   
cricket,The cricket is a insect    references to information about entities and t...   
ant,The ant is a insect            specific names and instances associated with c...   
mite,The mite is a in

## Heuristic Assessments
- Feature refer to animals?
- Feature refer to hyperonym?
- Feature refer to hyponym/hyponym word?
- (optional) Try to disentangle hyponym from mention (cat from "cat")

# TODO
- Check if a feature contains a word like animals, hyperonym or hyponim. (1,2, 3)
- Store a matrix len(df) * n_features with 0s when neither of the vaues (1,2,3) are spotted
- Plot a heatmap to have a sense of the distribution of the 3 target



#TODO2
- Embed each explanations and project them into a 2d space
    - We can embed unique sents to see recurrent sentences
- Plot circles? How to do it?


build the dataframe with



In [8]:
df = pd.read_csv("./topk_explanations2.tsv", sep = "\t", index_col= "Unnamed: 0"); df.head()

Top1_feature  \
lion,The lion is a mammal                       words and phrases related to animals   
llama,The llama is a mammal        numerical data and statistics related to incid...   
rabbit,The rabbit is a mammal      numerical data and statistics related to incid...   
mongoose,The mongoose is a mammal  terms related to the performance or descriptio...   
hamster,The hamster is a mammal                 words and phrases related to animals   

                                                                        Top2_feature  \
lion,The lion is a mammal          technical terms and keywords related to progra...   
llama,The llama is a mammal        elements related to academic citations and aff...   
rabbit,The rabbit is a mammal                   words and phrases related to animals   
mongoose,The mongoose is a mammal  references to specific names and titles in a n...   
hamster,The hamster is a mammal    numerical data and statistics related to incid...   

                                                                        Top3_feature  \
lion,The lion is a mammal          references to individual songs or personal nar...   
llama,The llama is a mammal                     words and phrases related to animals   
rabbit,The rabbit is a mammal      elements related to themes of social justice a...   
mongoose,The mongoose is a mammal  elements related to themes of social justice a...   
hamster,The hamster is a mammal    elements related to themes of social justice a...   

                                                                        Top4_feature  \
lion,The lion is a mammal          elements related to themes of social justice a...   
llama,The llama is a mammal        references to individual songs or personal nar...   
rabbit,The rabbit is a mammal      technical terms and keywords related to progra...   
mongoose,The mongoose is a mammal               words and phrases related to animals   
hamster,The hamster is a mammal    references to individual songs or personal nar...   

                                                                        Top5_feature  
lion,The lion is a mammal          details related to film production and notable...  
llama,The llama is a mammal        specific references to parts of plants or bota...  
rabbit,The rabbit is a mammal      sequences that denote data structures or code ...  
mongoose,The mongoose is a mammal  terms related to ecological and biological con...  
hamster,The hamster is a mammal        phrases associated with rodent-borne diseases

In [3]:
import requests
r = requests.get("https://neuronpedia-exports.s3.amazonaws.com/explanations-only/gemma-2-2b_25-gemmascope-res-16k.json")

print(r.json())

[{'modelId': 'gemma-2-2b', 'layer': '25-gemmascope-res-16k', 'index': '13447', 'description': ' hexadecimal color codes', 'explanationModelName': 'gpt-4o-mini', 'typeName': 'oai_token-act-pair'}, {'modelId': 'gemma-2-2b', 'layer': '25-gemmascope-res-16k', 'index': '34', 'description': 'references to customer support and service in eCommerce platforms', 'explanationModelName': 'gpt-4o-mini', 'typeName': 'oai_token-act-pair'}, {'modelId': 'gemma-2-2b', 'layer': '25-gemmascope-res-16k', 'index': '38', 'description': ' phrases related to collaboration and teamwork', 'explanationModelName': 'gpt-4o-mini', 'typeName': 'oai_token-act-pair'}, {'modelId': 'gemma-2-2b', 'layer': '25-gemmascope-res-16k', 'index': '173', 'description': 'references to conservation and environmental management activities', 'explanationModelName': 'gpt-4o-mini', 'typeName': 'oai_token-act-pair'}, {'modelId': 'gemma-2-2b', 'layer': '25-gemmascope-res-16k', 'index': '213', 'description': ' punctuation marks and statist

In [4]:
r.json()

[{'modelId': 'gemma-2-2b',
  'layer': '25-gemmascope-res-16k',
  'index': '13447',
  'description': ' hexadecimal color codes',
  'explanationModelName': 'gpt-4o-mini',
  'typeName': 'oai_token-act-pair'},
 {'modelId': 'gemma-2-2b',
  'layer': '25-gemmascope-res-16k',
  'index': '34',
  'description': 'references to customer support and service in eCommerce platforms',
  'explanationModelName': 'gpt-4o-mini',
  'typeName': 'oai_token-act-pair'},
 {'modelId': 'gemma-2-2b',
  'layer': '25-gemmascope-res-16k',
  'index': '38',
  'description': ' phrases related to collaboration and teamwork',
  'explanationModelName': 'gpt-4o-mini',
  'typeName': 'oai_token-act-pair'},
 {'modelId': 'gemma-2-2b',
  'layer': '25-gemmascope-res-16k',
  'index': '173',
  'description': 'references to conservation and environmental management activities',
  'explanationModelName': 'gpt-4o-mini',
  'typeName': 'oai_token-act-pair'},
 {'modelId': 'gemma-2-2b',
  'layer': '25-gemmascope-res-16k',
  'index': '213'